In [1]:
import pandas as pd
import h3
import geopandas as gpd

In [2]:
df = pd.read_csv("ALL/Audience_Profiles_Destination_2025-03-01_loco_all_tracks.tsv",sep='\t')

In [3]:
df.head()

CODE      ORIGIN_CODE  DAY_TYPE         DAY  MONTH  YEAR  \
0  8b1951b75430fff  8a1951b1e4a7fff         6  2025-03-01      3  2025   
1  8b195d821adcfff  8a195da58417fff         6  2025-03-01      3  2025   
2  8b1942005caafff  8a1942005caffff         6  2025-03-01      3  2025   
3  8b194e15e154fff  8a194e143507fff         6  2025-03-01      3  2025   
4  8b195dae5448fff  8a195daf036ffff         6  2025-03-01      3  2025   

  MOVEMENT_MODALITY  EXTRAPOLATED_NUMBER_OF_USERS  \
0               ALL                           6.0   
1               ALL                           6.0   
2               ALL                           6.0   
3               ALL                           6.0   
4               ALL                           6.0   

   EXTRAPOLATED_NUMBER_OF_SIGNALS  
0                             6.0  
1                             6.0  
2                             6.0  
3                             6.0  
4                             6.0

In [ ]:
import pandas as pd
import glob
import os

# Load and merge all tracking data files
# The following code uses glob to read all tsv files and combines them into one CSV

file_pattern = "ALL/Audience_Profiles_Destination_2025-03-*_loco_all_tracks.tsv"
print("Reading all files using glob pattern:", file_pattern)

all_files = glob.glob(file_pattern)
print(f"Found {len(all_files)} files")

dfs = []
for file in all_files:
    print(f"Reading file: {file}")
    df = pd.read_csv(file, sep='\t')
    # Keep only Monday to Thursday data
    df_filtered = df[df['DAY_OF_WEEK'].isin([1, 2, 3, 4])]
    print(f"Original {len(df)} rows, after filtering: {len(df_filtered)} rows")
    dfs.append(df_filtered)

combined_df = pd.concat(dfs, ignore_index=True)
print(f"Combined dataset: {len(combined_df)} rows")
combined_df.to_csv("all_core_weekday_tracks_2025-03.csv", index=False)
print("Saved as all_core_weekday_tracks_2025-03.csv")

核心工作日数据已合并并写入到 all_core_weekday_tracks_2025-03.csv


#### Correct data merging code

In [ ]:
import pandas as pd
import h3
import geopandas as gpd
from shapely.geometry import Point
import gc

# Load TTWA data
ttwa_gdf = gpd.read_file("boundary/Travel_to_Work_Areas_Dec_2011_FCB_in_United_Kingdom_2022.geojson")
ttwa_gdf = ttwa_gdf.to_crs('EPSG:4326')[['TTWA11NM', 'geometry']]

# Helper function to batch map H3 hexagons to TTWA names
def hex_to_ttwa_mapper(hex_list, ttwa_gdf, batch_size=500):
    """
    Batch process large number of hexagons to map to TTWA names
    Uses chunked processing to avoid memory issues
    """
    mapping = {}
    for i in range(0, len(hex_list), batch_size):
        batch = hex_list[i:i+batch_size]
        points = []
        valid_hexes = []
        
        for hex_id in batch:
            try:
                lat, lng = h3.cell_to_latlng(hex_id)
                points.append(Point(lng, lat))
                valid_hexes.append(hex_id)
            except:
                continue
        
        if valid_hexes:
            temp_gdf = gpd.GeoDataFrame({'hex_id': valid_hexes}, geometry=points, crs='EPSG:4326')
            joined = gpd.sjoin(temp_gdf, ttwa_gdf, how='left', predicate='within')
            for _, row in joined.iterrows():
                if pd.notna(row['TTWA11NM']):
                    mapping[row['hex_id']] = row['TTWA11NM']
            del temp_gdf, joined, points
            gc.collect()
    return mapping

# Process large file in chunks
chunksize = 100_000  # Adjust based on available memory
input_file = "all_core_weekday_tracks_2025-03.csv"
output_file = "od_data_with_ttwa.csv"
first_write = True

for chunk in pd.read_csv(input_file, chunksize=chunksize):
    # Process all unique hexagons from origin and destination
    all_hexes = pd.unique(chunk['CODE'].dropna().tolist() + chunk['ORIGIN_CODE'].dropna().tolist())
    hex_to_ttwa = hex_to_ttwa_mapper(all_hexes, ttwa_gdf, batch_size=500)
    # Map TTWA names
    chunk['dest_ttwa'] = chunk['CODE'].map(hex_to_ttwa)
    chunk['origin_ttwa'] = chunk['ORIGIN_CODE'].map(hex_to_ttwa)
    # Write to new file
    chunk.to_csv(output_file, mode='a', header=first_write, index=False)
    first_write = False
    print(f"Wrote {len(chunk)} rows...")

print("Chunked spatial join completed, results saved to", output_file)

正在分块读取文件...
已处理第 1 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 2 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 3 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 4 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 5 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 3 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 4 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 5 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 6 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 7 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 8 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 9 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 6 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 7 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 8 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 9 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 10 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 11 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 12 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 10 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 11 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 12 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 13 个chunk，当前发现的唯一DAY值: ['2025-03-11']
已处理第 14 个chunk，

/var/folders/c0/g_0prcks6s12wzk9s1vnm24w0000gn/T/ipykernel_8030/4129325297.py:10: DtypeWarning: Columns (2,4,5,7,8) have mixed types. Specify dtype option on import or set low_memory=False.
  for chunk in pd.read_csv('all_core_weekday_tracks_2025-03.csv', chunksize=chunk_size):


已处理第 3702 个chunk，当前发现的唯一DAY值: ['2025-03-03', '2025-03-04', '2025-03-05', '2025-03-06', '2025-03-10', '2025-03-11', '2025-03-12', '2025-03-13', '2025-03-17', '2025-03-18', '2025-03-19', '2025-03-20', '2025-03-24', '2025-03-25', '2025-03-26', '2025-03-27', '2025-03-31', 'DAY']
已处理第 3703 个chunk，当前发现的唯一DAY值: ['2025-03-03', '2025-03-04', '2025-03-05', '2025-03-06', '2025-03-10', '2025-03-11', '2025-03-12', '2025-03-13', '2025-03-17', '2025-03-18', '2025-03-19', '2025-03-20', '2025-03-24', '2025-03-25', '2025-03-26', '2025-03-27', '2025-03-31', 'DAY']
已处理第 3704 个chunk，当前发现的唯一DAY值: ['2025-03-03', '2025-03-04', '2025-03-05', '2025-03-06', '2025-03-10', '2025-03-11', '2025-03-12', '2025-03-13', '2025-03-17', '2025-03-18', '2025-03-19', '2025-03-20', '2025-03-24', '2025-03-25', '2025-03-26', '2025-03-27', '2025-03-31', 'DAY']
已处理第 3705 个chunk，当前发现的唯一DAY值: ['2025-03-03', '2025-03-04', '2025-03-05', '2025-03-06', '2025-03-10', '2025-03-11', '2025-03-12', '2025-03-13', '2025-03-17', '2025-03-18', '

### Extract H3 hexagon center coordinates and spatial join to TTWA

In [1]:
import pandas as pd
import h3
import geopandas as gpd
from shapely.geometry import Point
import gc

# 加载TTWA数据
ttwa_gdf = gpd.read_file("boundary/Travel_to_Work_Areas_Dec_2011_FCB_in_United_Kingdom_2022.geojson")
ttwa_gdf = ttwa_gdf.to_crs('EPSG:4326')
ttwa_gdf = ttwa_gdf[['TTWA11NM', 'geometry']]

def hex_to_ttwa_mapper(hex_codes, ttwa_gdf, batch_size=1000):
    """将一批H3六边形映射到TTWA名称"""
    mapping = {}
    for i in range(0, len(hex_codes), batch_size):
        batch = hex_codes[i:i+batch_size]
        points = []
        valid_hexes = []
        for hex_id in batch:
            try:
                lat, lng = h3.cell_to_latlng(hex_id)
                points.append(Point(lng, lat))
                valid_hexes.append(hex_id)
            except Exception:
                continue
        if valid_hexes:
            temp_gdf = gpd.GeoDataFrame({'hex_id': valid_hexes}, geometry=points, crs='EPSG:4326')
            joined = gpd.sjoin(temp_gdf, ttwa_gdf, how='left', predicate='within')
            for _, row in joined.iterrows():
                if pd.notna(row['TTWA11NM']):
                    mapping[row['hex_id']] = row['TTWA11NM']
            del temp_gdf, joined, points
            gc.collect()
    return mapping

# 分块处理大文件
chunksize = 100_000  # 可根据内存调整
input_file = "all_core_weekday_tracks_2025-03.csv"
output_file = "od_data_with_ttwa.csv"
first_write = True

for chunk in pd.read_csv(input_file, chunksize=chunksize):
    # 处理origin和dest所有唯一hex
    all_hexes = pd.unique(chunk['CODE'].dropna().tolist() + chunk['ORIGIN_CODE'].dropna().tolist())
    hex_to_ttwa = hex_to_ttwa_mapper(all_hexes, ttwa_gdf, batch_size=500)
    # 映射TTWA
    chunk['dest_ttwa'] = chunk['CODE'].map(hex_to_ttwa)
    chunk['origin_ttwa'] = chunk['ORIGIN_CODE'].map(hex_to_ttwa)
    # 写入新文件
    chunk.to_csv(output_file, mode='a', header=first_write, index=False)
    first_write = False
    print(f"写入 {len(chunk)} 行...")

print("分块空间连接完成，结果已保存到", output_file)

ModuleNotFoundError: No module named 'h3'

In [ ]:
import pandas as pd

print("Extracting all unique hexagon IDs...")
all_unique_hexes = set()

for chunk in pd.read_csv("all_core_weekday_tracks_2025-03.csv", chunksize=200_000):
    dest_hexes = chunk['CODE'].dropna().unique()
    origin_hexes = chunk['ORIGIN_CODE'].dropna().unique()
    all_unique_hexes.update(dest_hexes)
    all_unique_hexes.update(origin_hexes)
    print(f"Current cumulative unique hexagons: {len(all_unique_hexes)}")

all_unique_hexes = list(all_unique_hexes)
print(f"Total unique hexagons: {len(all_unique_hexes)}")

# Save results
pd.DataFrame({'hex_id': all_unique_hexes}).to_csv("unique_hexes.csv", index=False)

提取所有唯一六边形ID...
当前累计唯一六边形数: 273413
当前累计唯一六边形数: 458516
当前累计唯一六边形数: 607254
当前累计唯一六边形数: 734263
当前累计唯一六边形数: 845568
当前累计唯一六边形数: 945745
当前累计唯一六边形数: 1036451
当前累计唯一六边形数: 1120146
当前累计唯一六边形数: 1197383
当前累计唯一六边形数: 1268894
当前累计唯一六边形数: 1336264
当前累计唯一六边形数: 1399974
当前累计唯一六边形数: 1459338
当前累计唯一六边形数: 1516030
当前累计唯一六边形数: 1570402
当前累计唯一六边形数: 1621724
当前累计唯一六边形数: 1670788
当前累计唯一六边形数: 1718120
当前累计唯一六边形数: 1763099
当前累计唯一六边形数: 1806392
当前累计唯一六边形数: 1847776
当前累计唯一六边形数: 1887807
当前累计唯一六边形数: 1926707
当前累计唯一六边形数: 1963979
当前累计唯一六边形数: 2000236
当前累计唯一六边形数: 2034968
当前累计唯一六边形数: 2068980
当前累计唯一六边形数: 2102031
当前累计唯一六边形数: 2134102
当前累计唯一六边形数: 2165240
当前累计唯一六边形数: 2195719
当前累计唯一六边形数: 2224851
当前累计唯一六边形数: 2253145
当前累计唯一六边形数: 2280750
当前累计唯一六边形数: 2307732
当前累计唯一六边形数: 2334407
当前累计唯一六边形数: 2360103
当前累计唯一六边形数: 2385141
当前累计唯一六边形数: 2409741
当前累计唯一六边形数: 2433893
当前累计唯一六边形数: 2457067
当前累计唯一六边形数: 2479976
当前累计唯一六边形数: 2502279
当前累计唯一六边形数: 2524326
当前累计唯一六边形数: 2545787
当前累计唯一六边形数: 2567048
当前累计唯一六边形数: 2587822
当前累计唯一六边形数: 2607997
当前累计唯一六边形数: 2627728
当前累计唯一六边形数:

##### Currently optimized version for extracting unique hexagons

In [ ]:
# Optimized version: Extract all unique H3 hexagon IDs with early stopping mechanism
import pandas as pd
import time
from datetime import datetime

def extract_unique_hexes_optimized(input_file, output_file="unique_hexes.csv", chunksize=200_000, early_stop_threshold=10):
    """
    Optimized version: Extract all unique H3 hexagon IDs with early stopping mechanism
    
    Parameters:
    - input_file: Input CSV file path
    - output_file: Output CSV file path
    - chunksize: Number of rows to read per batch
    - early_stop_threshold: Stop if no new IDs found for this many consecutive batches
    """
    print(f"Starting unique hexagon ID extraction... Time: {datetime.now()}")
    print(f"Input file: {input_file}")
    print(f"Output file: {output_file}")
    print(f"Batch size: {chunksize:,}")
    print(f"Early stop threshold: {early_stop_threshold} batches")
    print("-" * 50)
    
    all_unique_hexes = set()
    consecutive_no_change = 0
    batch_count = 0
    start_time = time.time()
    
    try:
        for chunk in pd.read_csv(input_file, chunksize=chunksize):
            batch_count += 1
            old_count = len(all_unique_hexes)
            
            # Extract unique hexagon IDs
            dest_hexes = chunk['CODE'].dropna().unique()
            origin_hexes = chunk['ORIGIN_CODE'].dropna().unique()
            
            # Update set
            all_unique_hexes.update(dest_hexes)
            all_unique_hexes.update(origin_hexes)
            
            new_count = len(all_unique_hexes)
            new_added = new_count - old_count
            
            # Calculate processing speed
            elapsed_time = time.time() - start_time
            avg_time_per_batch = elapsed_time / batch_count
            
            print(f"Batch {batch_count:4d} | Unique hexagons: {new_count:,} | New: {new_added:,} | "
                  f"Time: {elapsed_time:.1f}s | Avg: {avg_time_per_batch:.2f}s/batch")
            
            # Early stopping mechanism
            if new_added == 0:
                consecutive_no_change += 1
                if consecutive_no_change >= early_stop_threshold:
                    print(f"\nWarning: No new additions for {early_stop_threshold} consecutive batches, early stopping triggered")
                    print(f"Processed {batch_count} batches, likely found all unique IDs")
                    break
            else:
                consecutive_no_change = 0
    
    except KeyboardInterrupt:
        print(f"\nWarning: User interrupted processing, processed {batch_count} batches")
    
    except Exception as e:
        print(f"\nError during processing: {e}")
    
    # Convert to list and save
    all_unique_hexes = list(all_unique_hexes)
    total_time = time.time() - start_time
    
    print("\n" + "="*50)
    print(f"Processing complete!")
    print(f"Total unique hexagons: {len(all_unique_hexes):,}")
    print(f"Batches processed: {batch_count}")
    print(f"Total time: {total_time:.1f} seconds ({total_time/60:.1f} minutes)")
    print(f"Average processing speed: {len(all_unique_hexes)/total_time:.0f} IDs/second")
    
    # Save results
    try:
        df_result = pd.DataFrame({'hex_id': all_unique_hexes})
        df_result.to_csv(output_file, index=False)
        print(f"Results saved to: {output_file}")
        
        # Show sample
        print(f"\nFirst 10 hexagon ID samples:")
        print(df_result.head(10)['hex_id'].tolist())
        
    except Exception as e:
        print(f"Error saving file: {e}")
    
    return all_unique_hexes

# Execute optimized version
unique_hexes = extract_unique_hexes_optimized(
    input_file="all_core_weekday_tracks_2025-03.csv",
    output_file="unique_hexes_optimized.csv",
    chunksize=200_000,
    early_stop_threshold=10
)

开始提取唯一六边形ID... 时间: 2025-06-20 18:45:10.958030
输入文件: all_core_weekday_tracks_2025-03.csv
输出文件: unique_hexes_optimized.csv
批次大小: 200,000
早停阈值: 10 个批次
--------------------------------------------------
批次    1 | 唯一六边形数: 274,340 | 新增: 274,340 | 用时: 0.2s | 平均: 0.23s/批次
批次    2 | 唯一六边形数: 460,184 | 新增: 185,844 | 用时: 0.4s | 平均: 0.21s/批次
批次    3 | 唯一六边形数: 609,741 | 新增: 149,557 | 用时: 0.6s | 平均: 0.20s/批次
批次    4 | 唯一六边形数: 737,181 | 新增: 127,440 | 用时: 0.8s | 平均: 0.19s/批次
批次    5 | 唯一六边形数: 849,414 | 新增: 112,233 | 用时: 1.0s | 平均: 0.19s/批次
批次    6 | 唯一六边形数: 950,297 | 新增: 100,883 | 用时: 1.1s | 平均: 0.19s/批次
批次    7 | 唯一六边形数: 1,041,270 | 新增: 90,973 | 用时: 1.3s | 平均: 0.19s/批次
批次    8 | 唯一六边形数: 1,125,451 | 新增: 84,181 | 用时: 1.5s | 平均: 0.19s/批次
批次    9 | 唯一六边形数: 1,203,388 | 新增: 77,937 | 用时: 1.7s | 平均: 0.19s/批次
批次   10 | 唯一六边形数: 1,275,850 | 新增: 72,462 | 用时: 1.9s | 平均: 0.19s/批次
批次   11 | 唯一六边形数: 1,343,750 | 新增: 67,900 | 用时: 2.1s | 平均: 0.19s/批次
批次   12 | 唯一六边形数: 1,407,875 | 新增: 64,125 | 用时: 2.4s | 平均: 0.20s/批次
批次 

/var/folders/c0/g_0prcks6s12wzk9s1vnm24w0000gn/T/ipykernel_13728/518263343.py:28: DtypeWarning: Columns (2,4,5,7,8) have mixed types. Specify dtype option on import or set low_memory=False.
  for chunk in pd.read_csv(input_file, chunksize=chunksize):


批次 1850 | 唯一六边形数: 5,371,567 | 新增: 136 | 用时: 410.6s | 平均: 0.22s/批次
批次 1851 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 410.9s | 平均: 0.22s/批次
批次 1851 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 410.9s | 平均: 0.22s/批次
批次 1852 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.1s | 平均: 0.22s/批次
批次 1852 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.1s | 平均: 0.22s/批次
批次 1853 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.3s | 平均: 0.22s/批次
批次 1853 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.3s | 平均: 0.22s/批次
批次 1854 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.5s | 平均: 0.22s/批次
批次 1854 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.5s | 平均: 0.22s/批次
批次 1855 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.7s | 平均: 0.22s/批次
批次 1855 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 411.7s | 平均: 0.22s/批次
批次 1856 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 412.0s | 平均: 0.22s/批次
批次 1856 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 412.0s | 平均: 0.22s/批次
批次 1857 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 412.2s | 平均: 0.22s/批次
批次 1857 | 唯一六边形数: 5,371,567 | 新增: 0 | 用时: 412.2s | 平均: 0.22s/批次
批次 1858 | 唯一六边形数: 5,371,567 | 新增: 0 | 

##### Hexagon to TTWA mapping relationship - second version is new

In [ ]:
import pandas as pd
import h3
import geopandas as gpd
from shapely.geometry import Point
import gc

# Load data
ttwa_gdf = gpd.read_file("boundary/Travel_to_Work_Areas_Dec_2011_FCB_in_United_Kingdom_2022.geojson")
ttwa_gdf = ttwa_gdf.to_crs('EPSG:4326')[['TTWA11NM', 'geometry']]

unique_hexes = pd.read_csv("unique_hexes.csv")['hex_id'].tolist()
print(f"Processing {len(unique_hexes)} unique hexagons")

# Build mapping in one pass
global_mapping = {}
batch_size = 5000

for i in range(0, len(unique_hexes), batch_size):
    batch = unique_hexes[i:i+batch_size]
    print(f"Batch {i//batch_size + 1}/{(len(unique_hexes)-1)//batch_size + 1}")
    
    points = []
    valid_hexes = []
    
    for hex_id in batch:
        try:
            lat, lng = h3.cell_to_latlng(hex_id)
            points.append(Point(lng, lat))
            valid_hexes.append(hex_id)
        except:
            continue
    
    if valid_hexes:
        temp_gdf = gpd.GeoDataFrame({'hex_id': valid_hexes}, geometry=points, crs='EPSG:4326')
        joined = gpd.sjoin(temp_gdf, ttwa_gdf, how='left', predicate='within')
        
        for _, row in joined.iterrows():
            if pd.notna(row['TTWA11NM']):
                global_mapping[row['hex_id']] = row['TTWA11NM']
        
        del temp_gdf, joined, points
        gc.collect()

# Save mapping table
mapping_df = pd.DataFrame(list(global_mapping.items()), columns=['hex_id', 'ttwa_name'])
mapping_df.to_csv("hex_to_ttwa_mapping.csv", index=False)
print(f"Mapping table saved: {len(global_mapping)} mapping relationships")

处理 5371565 个唯一六边形
批次 1/1075
批次 2/1075
批次 3/1075
批次 4/1075
批次 5/1075
批次 6/1075
批次 7/1075
批次 8/1075
批次 9/1075
批次 10/1075
批次 11/1075
批次 12/1075
批次 13/1075
批次 14/1075
批次 15/1075
批次 16/1075
批次 17/1075
批次 18/1075
批次 19/1075
批次 20/1075
批次 21/1075
批次 22/1075
批次 23/1075
批次 24/1075
批次 25/1075
批次 26/1075
批次 27/1075
批次 28/1075
批次 29/1075
批次 30/1075
批次 31/1075
批次 32/1075
批次 33/1075
批次 34/1075
批次 35/1075
批次 36/1075
批次 37/1075
批次 38/1075
批次 39/1075
批次 40/1075
批次 41/1075
批次 42/1075
批次 43/1075
批次 44/1075
批次 45/1075
批次 46/1075
批次 47/1075
批次 48/1075
批次 49/1075
批次 50/1075
批次 51/1075
批次 52/1075
批次 53/1075
批次 54/1075
批次 55/1075
批次 56/1075
批次 57/1075
批次 58/1075
批次 59/1075
批次 60/1075
批次 61/1075
批次 62/1075
批次 63/1075
批次 64/1075
批次 65/1075
批次 66/1075
批次 67/1075
批次 68/1075
批次 69/1075
批次 70/1075
批次 71/1075
批次 72/1075
批次 73/1075
批次 74/1075
批次 75/1075
批次 76/1075
批次 77/1075
批次 78/1075
批次 79/1075
批次 80/1075
批次 81/1075
批次 82/1075
批次 83/1075
批次 84/1075
批次 85/1075
批次 86/1075
批次 87/1075
批次 88/1075
批次 89/1075
批次 90/1075
批

In [ ]:
import pandas as pd
import h3
import geopandas as gpd
from shapely.geometry import Point
import gc

# Load data
ttwa_gdf = gpd.read_file("boundary/Travel_to_Work_Areas_Dec_2011_FCB_in_United_Kingdom_2022.geojson")
ttwa_gdf = ttwa_gdf.to_crs('EPSG:4326')[['TTWA11NM', 'geometry']]

unique_hexes = pd.read_csv("unique_hexes_optimized.csv")['hex_id'].tolist()
print(f"Processing {len(unique_hexes)} unique hexagons")

# Build mapping in one pass
global_mapping = {}
batch_size = 5000

for i in range(0, len(unique_hexes), batch_size):
    batch = unique_hexes[i:i+batch_size]
    print(f"Batch {i//batch_size + 1}/{(len(unique_hexes)-1)//batch_size + 1}")
    
    points = []
    valid_hexes = []
    
    for hex_id in batch:
        try:
            lat, lng = h3.cell_to_latlng(hex_id)
            points.append(Point(lng, lat))
            valid_hexes.append(hex_id)
        except:
            continue
    
    if valid_hexes:
        temp_gdf = gpd.GeoDataFrame({'hex_id': valid_hexes}, geometry=points, crs='EPSG:4326')
        joined = gpd.sjoin(temp_gdf, ttwa_gdf, how='left', predicate='within')
        
        for _, row in joined.iterrows():
            if pd.notna(row['TTWA11NM']):
                global_mapping[row['hex_id']] = row['TTWA11NM']
        
        del temp_gdf, joined, points
        gc.collect()

# Save mapping table
mapping_df = pd.DataFrame(list(global_mapping.items()), columns=['hex_id', 'ttwa_name'])
mapping_df.to_csv("hex_to_ttwa_mapping.csv", index=False)
print(f"Mapping table saved: {len(global_mapping)} mapping relationships")

处理 5371567 个唯一六边形
批次 1/1075
批次 2/1075
批次 3/1075
批次 4/1075
批次 5/1075
批次 6/1075
批次 7/1075
批次 8/1075
批次 9/1075
批次 10/1075
批次 11/1075
批次 12/1075
批次 13/1075
批次 14/1075
批次 15/1075
批次 16/1075
批次 17/1075
批次 18/1075
批次 19/1075
批次 20/1075
批次 21/1075
批次 22/1075
批次 23/1075
批次 24/1075
批次 25/1075
批次 26/1075
批次 27/1075
批次 28/1075
批次 29/1075
批次 30/1075
批次 31/1075
批次 32/1075
批次 33/1075
批次 34/1075
批次 35/1075
批次 36/1075
批次 37/1075
批次 38/1075
批次 39/1075
批次 40/1075
批次 41/1075
批次 42/1075
批次 43/1075
批次 44/1075
批次 45/1075
批次 46/1075
批次 47/1075
批次 48/1075
批次 49/1075
批次 50/1075
批次 51/1075
批次 52/1075
批次 53/1075
批次 54/1075
批次 55/1075
批次 56/1075
批次 57/1075
批次 58/1075
批次 59/1075
批次 60/1075
批次 61/1075
批次 62/1075
批次 63/1075
批次 64/1075
批次 65/1075
批次 66/1075
批次 67/1075
批次 68/1075
批次 69/1075
批次 70/1075
批次 71/1075
批次 72/1075
批次 73/1075
批次 74/1075
批次 75/1075
批次 76/1075
批次 77/1075
批次 78/1075
批次 79/1075
批次 80/1075
批次 81/1075
批次 82/1075
批次 83/1075
批次 84/1075
批次 85/1075
批次 86/1075
批次 87/1075
批次 88/1075
批次 89/1075
批次 90/1075
批

In [ ]:
import pandas as pd

# Load mapping table
hex_to_ttwa_mapping = pd.read_csv("hex_to_ttwa_mapping.csv").set_index('hex_id')['ttwa_name'].to_dict()

# Use larger chunk_size for improved efficiency
ttwa_od_external = []
batch_num = 0

for chunk in pd.read_csv("all_core_weekday_tracks_2025-03.csv", chunksize=500_000):  # Increased to 500k
    batch_num += 1
    
    # Fast mapping
    chunk['dest_ttwa'] = chunk['CODE'].map(hex_to_ttwa_mapping)
    chunk['origin_ttwa'] = chunk['ORIGIN_CODE'].map(hex_to_ttwa_mapping)
    
    # Cross-city flows
    cross_city_chunk = chunk[
        (chunk['dest_ttwa'].notna()) & 
        (chunk['origin_ttwa'].notna()) & 
        (chunk['dest_ttwa'] != chunk['origin_ttwa'])
    ]
    
    if len(cross_city_chunk) > 0:
        # Fix data type issues
        # 1. Convert EXTRAPOLATED_NUMBER_OF_USERS to numeric type, set invalid values to 0
        cross_city_chunk = cross_city_chunk.copy()
        cross_city_chunk['EXTRAPOLATED_NUMBER_OF_USERS'] = pd.to_numeric(
            cross_city_chunk['EXTRAPOLATED_NUMBER_OF_USERS'], 
            errors='coerce'  # Set unconvertible values to NaN
        ).fillna(0)  # Fill NaN with 0
        
        # 2. Filter out records with 0 users (optional)
        cross_city_chunk = cross_city_chunk[cross_city_chunk['EXTRAPOLATED_NUMBER_OF_USERS'] > 0]
        
        if len(cross_city_chunk) > 0:
            chunk_od = cross_city_chunk.groupby(['origin_ttwa', 'dest_ttwa'])['EXTRAPOLATED_NUMBER_OF_USERS'].sum().reset_index()
            ttwa_od_external.append(chunk_od)
            print(f"Batch {batch_num}: Cross-city {len(cross_city_chunk)} rows → OD pairs {len(chunk_od)}")
        else:
            print(f"Batch {batch_num}: No valid records after data cleaning")

# Merge results
final_od = pd.concat(ttwa_od_external, ignore_index=True)
final_od = final_od.groupby(['origin_ttwa', 'dest_ttwa'])['EXTRAPOLATED_NUMBER_OF_USERS'].sum().reset_index()
final_od.columns = ['ORIGIN_TTWA', 'DEST_TTWA', 'TOTAL_FLOW']
final_od = final_od.sort_values('TOTAL_FLOW', ascending=False)

final_od.to_csv("ttwa_od_matrix_cross_city_only.csv", index=False)
print(f"Complete! Cross-city OD pairs: {len(final_od)}")

批次 1: 跨城市 85616 行 → OD对 5557
批次 2: 跨城市 85280 行 → OD对 5580
批次 2: 跨城市 85280 行 → OD对 5580
批次 3: 跨城市 85500 行 → OD对 5509
批次 3: 跨城市 85500 行 → OD对 5509
批次 4: 跨城市 84880 行 → OD对 5611
批次 4: 跨城市 84880 行 → OD对 5611
批次 5: 跨城市 85734 行 → OD对 5606
批次 5: 跨城市 85734 行 → OD对 5606
批次 6: 跨城市 85530 行 → OD对 5531
批次 6: 跨城市 85530 行 → OD对 5531
批次 7: 跨城市 85069 行 → OD对 5484
批次 7: 跨城市 85069 行 → OD对 5484
批次 8: 跨城市 85540 行 → OD对 5594
批次 8: 跨城市 85540 行 → OD对 5594
批次 9: 跨城市 85388 行 → OD对 5551
批次 9: 跨城市 85388 行 → OD对 5551
批次 10: 跨城市 85564 行 → OD对 5535
批次 10: 跨城市 85564 行 → OD对 5535
批次 11: 跨城市 85414 行 → OD对 5596
批次 11: 跨城市 85414 行 → OD对 5596
批次 12: 跨城市 84856 行 → OD对 5593
批次 12: 跨城市 84856 行 → OD对 5593
批次 13: 跨城市 85574 行 → OD对 5568
批次 13: 跨城市 85574 行 → OD对 5568
批次 14: 跨城市 85288 行 → OD对 5570
批次 14: 跨城市 85288 行 → OD对 5570
批次 15: 跨城市 86053 行 → OD对 5634
批次 15: 跨城市 86053 行 → OD对 5634
批次 16: 跨城市 85409 行 → OD对 5619
批次 16: 跨城市 85409 行 → OD对 5619
批次 17: 跨城市 84744 行 → OD对 5554
批次 17: 跨城市 84744 行 → OD对 5554
批次 18: 跨城市 85296 行 → OD对 55

/var/folders/c0/g_0prcks6s12wzk9s1vnm24w0000gn/T/ipykernel_13728/423611970.py:10: DtypeWarning: Columns (2,4,5,7,8) have mixed types. Specify dtype option on import or set low_memory=False.
  for chunk in pd.read_csv("all_core_weekday_tracks_2025-03.csv", chunksize=500_000):  # 增加到50万


批次 740: 跨城市 89384 行 → OD对 5907
批次 741: 跨城市 85504 行 → OD对 5601
批次 741: 跨城市 85504 行 → OD对 5601
批次 742: 跨城市 85478 行 → OD对 5515
批次 742: 跨城市 85478 行 → OD对 5515
批次 743: 跨城市 85248 行 → OD对 5562
批次 743: 跨城市 85248 行 → OD对 5562
批次 744: 跨城市 85130 行 → OD对 5609
批次 744: 跨城市 85130 行 → OD对 5609
批次 745: 跨城市 85776 行 → OD对 5628
批次 745: 跨城市 85776 行 → OD对 5628
批次 746: 跨城市 85301 行 → OD对 5519
批次 746: 跨城市 85301 行 → OD对 5519
批次 747: 跨城市 85293 行 → OD对 5527
批次 747: 跨城市 85293 行 → OD对 5527
批次 748: 跨城市 85701 行 → OD对 5629
批次 748: 跨城市 85701 行 → OD对 5629
批次 749: 跨城市 85150 行 → OD对 5544
批次 749: 跨城市 85150 行 → OD对 5544
批次 750: 跨城市 85395 行 → OD对 5494
批次 750: 跨城市 85395 行 → OD对 5494
批次 751: 跨城市 85540 行 → OD对 5604
批次 751: 跨城市 85540 行 → OD对 5604
批次 752: 跨城市 84806 行 → OD对 5564
批次 752: 跨城市 84806 行 → OD对 5564
批次 753: 跨城市 85664 行 → OD对 5566
批次 753: 跨城市 85664 行 → OD对 5566
批次 754: 跨城市 85490 行 → OD对 5597
批次 754: 跨城市 85490 行 → OD对 5597
批次 755: 跨城市 85824 行 → OD对 5579
批次 755: 跨城市 85824 行 → OD对 5579
批次 756: 跨城市 85262 行 → OD对 5556
批次 756: 

/var/folders/c0/g_0prcks6s12wzk9s1vnm24w0000gn/T/ipykernel_13728/423611970.py:10: DtypeWarning: Columns (2,4,5,7,8) have mixed types. Specify dtype option on import or set low_memory=False.
  for chunk in pd.read_csv("all_core_weekday_tracks_2025-03.csv", chunksize=500_000):  # 增加到50万


批次 1480: 跨城市 88096 行 → OD对 5886
批次 1481: 跨城市 85416 行 → OD对 5603
批次 1481: 跨城市 85416 行 → OD对 5603
批次 1482: 跨城市 85517 行 → OD对 5552
批次 1482: 跨城市 85517 行 → OD对 5552
批次 1483: 跨城市 84940 行 → OD对 5527
批次 1483: 跨城市 84940 行 → OD对 5527
批次 1484: 跨城市 85465 行 → OD对 5610
批次 1484: 跨城市 85465 行 → OD对 5610
批次 1485: 跨城市 85659 行 → OD对 5567
批次 1485: 跨城市 85659 行 → OD对 5567
批次 1486: 跨城市 85278 行 → OD对 5514
批次 1486: 跨城市 85278 行 → OD对 5514
批次 1487: 跨城市 85374 行 → OD对 5540
批次 1487: 跨城市 85374 行 → OD对 5540
批次 1488: 跨城市 85399 行 → OD对 5607
批次 1488: 跨城市 85399 行 → OD对 5607
批次 1489: 跨城市 85343 行 → OD对 5564
批次 1489: 跨城市 85343 行 → OD对 5564
批次 1490: 跨城市 85409 行 → OD对 5531
批次 1490: 跨城市 85409 行 → OD对 5531
批次 1491: 跨城市 85567 行 → OD对 5612
批次 1491: 跨城市 85567 行 → OD对 5612
批次 1492: 跨城市 85067 行 → OD对 5545
批次 1492: 跨城市 85067 行 → OD对 5545
批次 1493: 跨城市 85501 行 → OD对 5570
批次 1493: 跨城市 85501 行 → OD对 5570
批次 1494: 跨城市 85545 行 → OD对 5621
批次 1494: 跨城市 85545 行 → OD对 5621
批次 1495: 跨城市 85744 行 → OD对 5622
批次 1495: 跨城市 85744 行 → OD对 5622
批次 1496:

In [ ]:
# High-performance optimized version - Significantly improved processing speed
import pandas as pd
import numpy as np
from collections import defaultdict
import time
import gc

def process_od_matrix_ultra_fast():
    """
    Ultra-fast OD matrix processing - Multiple optimization strategies
    Expected performance improvement: 3-5x
    """
    
    print("Starting ultra-fast OD matrix processing...")
    start_time = time.time()
    
    # 1. Pre-load mapping table as set for faster lookup
    print("Loading mapping table...")
    hex_to_ttwa_mapping = pd.read_csv("hex_to_ttwa_mapping.csv").set_index('hex_id')['ttwa_name'].to_dict()
    valid_hexes = set(hex_to_ttwa_mapping.keys())  # Pre-create set for fast lookup
    print(f"Mapping table contains {len(hex_to_ttwa_mapping):,} valid hexagons")
    
    # 2. Use dictionary accumulator to avoid frequent DataFrame operations
    od_accumulator = defaultdict(float)
    batch_num = 0
    total_processed = 0
    
    # 3. Optimize parameters
    CHUNK_SIZE = 1_000_000  # Increased to 1 million rows
    DTYPE_SPEC = {
        'CODE': 'str',
        'ORIGIN_CODE': 'str', 
        'EXTRAPOLATED_NUMBER_OF_USERS': 'str'  # Read as string first, process uniformly
    }
    
    print(f"Configuration: Batch size={CHUNK_SIZE:,}, using dictionary accumulator")
    print("-" * 60)
    
    try:
        # 4. Read data with specified columns and data types to reduce memory overhead
        csv_reader = pd.read_csv(
            "all_core_weekday_tracks_2025-03.csv", 
            chunksize=CHUNK_SIZE,
            dtype=DTYPE_SPEC,
            usecols=['CODE', 'ORIGIN_CODE', 'EXTRAPOLATED_NUMBER_OF_USERS']  # Only read needed columns
        )
        
        for chunk in csv_reader:
            batch_num += 1
            batch_start = time.time()
            
            # 5. Pre-filter: keep only hexagons with mappings
            chunk = chunk[
                chunk['CODE'].isin(valid_hexes) & 
                chunk['ORIGIN_CODE'].isin(valid_hexes)
            ].copy()
            
            if len(chunk) == 0:
                print(f"Batch {batch_num}: No valid data, skipping")
                continue
            
            # 6. Batch map TTWA
            chunk['dest_ttwa'] = chunk['CODE'].map(hex_to_ttwa_mapping)
            chunk['origin_ttwa'] = chunk['ORIGIN_CODE'].map(hex_to_ttwa_mapping)
            
            # 7. Filter cross-city flows
            cross_city_mask = (chunk['dest_ttwa'] != chunk['origin_ttwa'])
            cross_city_chunk = chunk[cross_city_mask].copy()
            
            if len(cross_city_chunk) == 0:
                print(f"Batch {batch_num}: No cross-city flows, skipping")
                continue
            
            # 8. Efficient numeric conversion
            users = pd.to_numeric(cross_city_chunk['EXTRAPOLATED_NUMBER_OF_USERS'], errors='coerce').fillna(0)
            valid_mask = users > 0
            
            if not valid_mask.any():
                print(f"Batch {batch_num}: No valid records after data cleaning")
                continue
            
            # 9. Use numpy for high-speed accumulation
            origins = cross_city_chunk.loc[valid_mask, 'origin_ttwa'].values
            dests = cross_city_chunk.loc[valid_mask, 'dest_ttwa'].values
            flows = users[valid_mask].values
            
            # 10. Directly accumulate to dictionary, avoiding intermediate DataFrames
            for origin, dest, flow in zip(origins, dests, flows):
                od_accumulator[(origin, dest)] += flow
            
            batch_time = time.time() - batch_start
            total_processed += len(cross_city_chunk)
            
            print(f"Batch {batch_num}: Processed {len(cross_city_chunk):,} rows | "
                  f"Cumulative OD pairs: {len(od_accumulator):,} | "
                  f"Time: {batch_time:.1f}s | "
                  f"Speed: {len(chunk)/batch_time:,.0f} rows/sec")
            
            # 11. Periodic memory cleanup
            if batch_num % 10 == 0:
                gc.collect()
        
    except Exception as e:
        print(f"Error during processing: {e}")
        print(f"Processed {batch_num} batches, will save partial results")
    
    # 12. Efficiently convert to DataFrame
    print("\nGenerating final OD matrix...")
    if od_accumulator:
        od_data = [
            {'ORIGIN_TTWA': origin, 'DEST_TTWA': dest, 'TOTAL_FLOW': flow}
            for (origin, dest), flow in od_accumulator.items()
        ]
        final_od = pd.DataFrame(od_data)
        final_od = final_od.sort_values('TOTAL_FLOW', ascending=False)
        
        # Save results
        output_file = "ttwa_od_matrix_cross_city_ultra_fast.csv"
        final_od.to_csv(output_file, index=False)
        
        total_time = time.time() - start_time
        
        print("\n" + "="*60)
        print("Processing complete!")
        print(f"Performance statistics:")
        print(f"   - Processing batches: {batch_num}")
        print(f"   - Total processed rows: {total_processed:,}")
        print(f"   - Cross-city OD pairs: {len(final_od):,}")
        print(f"   - Total time: {total_time:.1f} seconds ({total_time/60:.1f} minutes)")
        print(f"   - Processing speed: {total_processed/total_time:,.0f} rows/sec")
        print(f"   - Total flow: {final_od['TOTAL_FLOW'].sum():,.0f}")
        print(f"Results saved to: {output_file}")
        
        # Show TOP 10
        print(f"\nTop 10 highest flow OD pairs:")
        print(final_od.head(10).to_string(index=False))
        
        return final_od
    else:
        print("No valid cross-city flow data found")
        return None

# Execute optimized processing
result = process_od_matrix_ultra_fast()

🚀 启动超高速OD矩阵处理...
📋 加载映射表...
映射表包含 5,334,882 个有效六边形
⚙️ 配置: 批次大小=1,000,000, 使用字典累加器
------------------------------------------------------------
批次 1: 处理 170,896 行 | 累计OD对: 7,151 | 用时: 4.6s | 速度: 202,707 行/秒
批次 2: 处理 170,380 行 | 累计OD对: 8,941 | 用时: 4.5s | 速度: 207,889 行/秒
批次 3: 处理 171,264 行 | 累计OD对: 10,029 | 用时: 4.5s | 速度: 207,730 行/秒
批次 4: 处理 170,609 行 | 累计OD对: 10,826 | 用时: 4.4s | 速度: 211,220 行/秒
批次 5: 处理 170,952 行 | 累计OD对: 11,455 | 用时: 4.3s | 速度: 213,566 行/秒
批次 6: 处理 170,270 行 | 累计OD对: 12,001 | 用时: 4.3s | 速度: 214,429 行/秒
批次 7: 处理 170,862 行 | 累计OD对: 12,463 | 用时: 4.5s | 速度: 206,333 行/秒
批次 8: 处理 171,462 行 | 累计OD对: 12,861 | 用时: 4.4s | 速度: 209,923 行/秒
批次 9: 处理 170,040 行 | 累计OD对: 13,191 | 用时: 4.4s | 速度: 212,168 行/秒
批次 10: 处理 170,837 行 | 累计OD对: 13,456 | 用时: 4.4s | 速度: 210,194 行/秒
批次 11: 处理 170,565 行 | 累计OD对: 13,737 | 用时: 4.6s | 速度: 200,590 行/秒
批次 12: 处理 170,818 行 | 累计OD对: 13,956 | 用时: 4.4s | 速度: 211,406 行/秒
批次 13: 处理 170,957 行 | 累计OD对: 14,217 | 用时: 4.4s | 速度: 212,358 行/秒
批次 14: 处理 170,877 行 | 累

In [1]:
ck = pd.read_csv("ttwa_od_matrix_cross_city_ultra_fast.csv")
print(ck.head(100))

NameError: name 'pd' is not defined

In [ ]:
# Check if TTWA names have variants
od = pd.read_csv("ttwa_od_matrix_cross_city_only.csv")
print(f"Actual OD pair count: {len(od)}")
print(f"Unique origin TTWAs: {od['ORIGIN_TTWA'].nunique()}")
print(f"Unique destination TTWAs: {od['DEST_TTWA'].nunique()}")

# Check for name variants
all_cities = set(od['ORIGIN_TTWA']).union(set(od['DEST_TTWA']))
print(f"Total unique cities: {len(all_cities)}")

# View possible duplicate names
city_names = sorted(list(all_cities))
for i, city in enumerate(city_names[:20]):
    print(f"{i+1:2d}. {city}")

实际OD对数量: 27021
唯一起点TTWA: 223
唯一终点TTWA: 224
总唯一城市数: 224
 1. Aberdeen
 2. Aberystwyth
 3. Alness and Invergordon
 4. Andover
 5. Arbroath and Montrose
 6. Ashford
 7. Aviemore and Grantown-on-Spey
 8. Ayr
 9. Ballymena
10. Banbury
11. Bangor and Holyhead
12. Barnsley
13. Barnstaple
14. Barrow-in-Furness
15. Basingstoke
16. Bath
17. Bedford
18. Belfast
19. Berwick
20. Bideford


In [ ]:
# Check mapping table
mapping = pd.read_csv("hex_to_ttwa_mapping.csv")
print(f"Unique TTWA count in mapping table: {mapping['ttwa_name'].nunique()}")
print(f"TTWA name samples:")
for name in mapping['ttwa_name'].value_counts().head(10).index:
    print(f"  {name}")

映射表中唯一TTWA数量: 224
TTWA名称样本:
  London
  Manchester
  Birmingham
  Leeds
  Sheffield
  Slough and Heathrow
  Warrington and Wigan
  Doncaster
  Luton
  Newcastle


In [ ]:
import pandas as pd
import networkx as nx
import numpy as np
import json
from collections import defaultdict
import matplotlib.pyplot as plt

# Step 1: Read data and calculate dependency weights
def calculate_dependency_weights(df):
    """
    Calculate dependency weights w_ij = t_ij / Σ_j t_ij
    where t_ij is the commuting flow from i to j
    """
    # Calculate total outflow for each origin city
    total_outflow = df.groupby('ORIGIN_TTWA')['TOTAL_FLOW'].sum()
    
    # Calculate dependency weights
    df['dependency_weight'] = df.apply(
        lambda row: row['TOTAL_FLOW'] / total_outflow[row['ORIGIN_TTWA']], 
        axis=1
    )
    
    return df

# Read data
df = pd.read_csv('ttwa_od_matrix_cross_city_only.csv')
df_with_weights = calculate_dependency_weights(df)

print(f"Data overview: {len(df)} OD records, {df['ORIGIN_TTWA'].nunique()} origin cities")
print(f"Dependency weight range: {df_with_weights['dependency_weight'].min():.6f} - {df_with_weights['dependency_weight'].max():.6f}")

数据概况：27021 条OD记录，223 个起点城市
依赖权重范围：0.000000 - 0.932935


In [ ]:
# Step 2: Build directed commuting network
def build_commuting_network(df_weights):
    """Build directed commuting network"""
    G = nx.DiGraph()
    
    # Add edges with dependency weights
    for _, row in df_weights.iterrows():
        G.add_edge(
            row['ORIGIN_TTWA'], 
            row['DEST_TTWA'], 
            weight=row['dependency_weight'],
            flow=row['TOTAL_FLOW']
        )
    
    return G

G = build_commuting_network(df_with_weights)
print(f"Network scale: {G.number_of_nodes()} nodes, {G.number_of_edges()} edges")

网络规模：224 个节点，27021 条边
